# Baby Names - Names Finding and Response Generation

This notebook is the AI-based heart for the project TheName 👶🏽✨. It shows how to, based on an input questionnaire fulfilled by users describing their family's key values, interests, and preferences for the name of an upcoming baby.

## Setup

### Installation

The necessary dependencies in the `requirements.txt` file (in the parent folder of this notebook). You should install them. It's recommended to use a virtual environment to manage dependencies.

### Database Generation

In order for this notebook to work, we need to have some database of names to find our perfect names in. You can generate an example synthetic database with the notebook `db-generation-girl-names.ipynb`.

### Imports

In [1]:
import sys, os
from flask import Request

# Add the root directory to the Python path
sys.path.append(os.path.abspath(os.path.join('..')))

from utils import * # Helper Functions

/Users/elenamatay/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


### Environment variables

**⚠️ Important Note ⚠️:** To run this notebook, you will need to place environment variables such as the project ID and region in the `utils.py` file. This file is located in the parent folder of this notebook.

### Helper functions

Helper functions can be found in the `utils.py` file. A summary of all functions used in this notebook can be found here:

- `read_object` - Reads an object from a GCS bucket. In this case, it's used to retrieve our names database (master JSON file) before filtering.

- `filter_names` - Based on the information fulfilled by users in the preferences questionnaire (baby's gender, origins to explore, desired syllables number and attributes for the name), we will filter the relevant names from our database.

- `generate` - Based on the filtered list of names and the users preferences, it finds the top 10 most relevant names for the family.

## Find the perfect names for a family's input form.

A family member will fulfill an input questionnaire on their name's preferences:
- Baby's gender (if known)
- Origins to lookup in (+30 available)
- Name's length
- Values and interests of the family
- Name attributes, e.g. modern, classic, edgy, earthy, etc.
- (Optional) Names to avoid, e.g. siblings name, names they don't like

That questionnaire's data will be passed in the form of an HTTP request to a Cloud Function. Example:
```
curl -X POST http://localhost:8080/ -H "Content-Type: application/json" -d '{
  "form_data": {
    "gender": "Girl",
    "origin": ["Spanish", "Italian", "Greek"],
    "attributes": ["Classic", "Modern", "Popular", "Famous and Historical"],
    "length": ["short", "medium"],
    "values": "Honesty, loyalty, open-mindness and critical thinking. We love playing sports, especially outdoors, and going to the mountain together during the weekends."
  }
}'
```

The Cloud Function will then do two main things:
1. Perform a filter to lookup on our database, returning only the relevant names for the baby (typically 500-1000 names)
2. Select the top 10 names from the filtered list that better match the family's preferences, and formulate the response in the form of a JSON, describing each name, its origin, meaning, and a custom description on why it is perfect for this family - Using Gemini.

In order not to need to deploy a Cloud Function, we pasted the code for the Cloud Function entry point (`generate_names`) in the cell below. You also have a sample request you can edit as you consider.

In [2]:
def generate_names(request):
    print("Received request")
    request_json = request.get_json(silent=True)
    request_args = request.args

    # Log the received JSON
    print(f"Received JSON: {request_json}")

    # Extract form_data from the request
    if request_json and "form_data" in request_json:
        form_data = request_json["form_data"]
    elif request_args and "form_data" in request_args:
        form_data = request_args["form_data"]
    else:
        retval = json.dumps({ "error": "no input form data in request"})
        print(f"Response: {retval}")
        return retval
    
    # Log the extracted form_data
    print(f"Extracted form_data: {form_data}")

    # Extract model_id from the request or use default
    if request_json and "model_id" in request_json:
        model_id = request_json["model_id"]
    elif request_args and "model_id" in request_args:
        model_id = request_args["model_id"]
    else:
        model_id = "gemini-1.5-flash-002"
        print(f"Set model default: {model_id}")

    # Filter the names based on the form data
    filtered_names = filter_names(form_data)
        
    # Generate the response using the provided details
    response = generate(form_data, filtered_names, model_id)
    return response

In [4]:
# Mock the request data
request_data = {
    "form_data": {
        "gender": "Girl",
        "origin": ["Spanish", "Italian", "Greek"],
        "attributes": ["Classic", "Modern", "Popular", "Famous and Historical"],
        "length": ["short", "medium"],
        "values": "Honesty, loyalty, open-mindness and critical thinking. We love playing sports, especially outdoors, and going to the mountain together during the weekends."
    }
}

# Create a mock request object
mock_request = Request.from_values(
    data=json.dumps(request_data),
    content_type='application/json'
)

# Call the function with the mock request
response = generate_names(mock_request)
print(json.dumps(json.loads(response), indent=4, ensure_ascii=False))

Received request
Received JSON: {'form_data': {'gender': 'Girl', 'origin': ['Spanish', 'Italian', 'Greek'], 'attributes': ['Classic', 'Modern', 'Popular', 'Famous and Historical'], 'length': ['short', 'medium'], 'values': 'Honesty, loyalty, open-mindness and critical thinking. We love playing sports, especially outdoors, and going to the mountain together during the weekends.'}}
Extracted form_data: {'gender': 'Girl', 'origin': ['Spanish', 'Italian', 'Greek'], 'attributes': ['Classic', 'Modern', 'Popular', 'Famous and Historical'], 'length': ['short', 'medium'], 'values': 'Honesty, loyalty, open-mindness and critical thinking. We love playing sports, especially outdoors, and going to the mountain together during the weekends.'}
Set model default: gemini-1.5-flash-002
Master JSON being used:{'Alva': {'meaning': 'elf friend', 'origin': ['German', 'Scandinavian'], 'sound_details': {'phonemes': ['æ', 'l', 'v', 'ə'], 'syllables': 2}, 'variants': ['Alvie', 'Alvo', 'Alva'], 'famous': ['Alva A